In [174]:
import pandas as pd
import json
import math
import re

# Función para agrupar mensajes de Remitentes

In [175]:
def agrupar_remitentes(texto_in):
    # Dividir el texto en líneas
    lineas = texto_in.strip().split('\n')

    # Procesar las líneas para agrupar los mensajes por remitente
    texto_out = ""
    ultimo_remitente = ""
    timestamp_actual = ""

    for linea in lineas:
        # Verificar si la línea tiene un remitente (es decir, si es un nuevo mensaje)
        if re.match(r"\[\d{2}/\d{2}/\d{2}, \d{1,2}:\d{2}:\d{2} [a.p].m.\] \w+:", linea):
            timestamp, remitente, mensaje = re.match(r"(\[\d{2}/\d{2}/\d{2}, \d{1,2}:\d{2}:\d{2} [a.p].m.\]) (\w+): (.*)", linea).groups()
            # Si el remitente es diferente al último, se inicia un nuevo mensaje
            if remitente != ultimo_remitente:
                texto_out += f"{timestamp} {remitente}: {mensaje}\n"
                ultimo_remitente = remitente
                timestamp_actual = timestamp
            else:
                # Añadir el mensaje actual al último mensaje del mismo remitente
                texto_out = texto_out.strip() + "\n" + mensaje + "\n"
        else:
            # Si la línea no tiene remitente, se añade al mensaje actual
            texto_out = texto_out.strip() + "\n" + linea.strip() + "\n"

    texto_out = texto_out.strip()

    return texto_out

### Prueba

In [176]:
texto_in = """
[30/08/22, 4:11:28 p.m.] CarmenQ: Pues eso es bueno
[30/08/22, 4:11:33 p.m.] CarmenQ: Así te llenas cool
[30/08/22, 4:11:51 p.m.] Sebas: Pues si
[30/08/22, 4:11:55 p.m.] Sebas: Ya me la terminé
Ya voy a regresar
[30/08/22, 4:12:15 p.m.] CarmenQ: Que bueno
Ok amor
[30/08/22, 4:12:25 p.m.] CarmenQ: Mucha suerte
La verdad es que tengo mucho sueño
[30/08/22, 4:12:33 p.m.] Sebas: Gracias amorcito
Te amo mucho
[30/08/22, 4:12:40 p.m.] CarmenQ: Yo a ti
"""

# Imprimir el texto transformado
print(agrupar_remitentes(texto_in))

[30/08/22, 4:11:28 p.m.] CarmenQ: Pues eso es bueno
Así te llenas cool
[30/08/22, 4:11:51 p.m.] Sebas: Pues si
Ya me la terminé
Ya voy a regresar
[30/08/22, 4:12:15 p.m.] CarmenQ: Que bueno
Ok amor
Mucha suerte
La verdad es que tengo mucho sueño
[30/08/22, 4:12:33 p.m.] Sebas: Gracias amorcito
Te amo mucho
[30/08/22, 4:12:40 p.m.] CarmenQ: Yo a ti


# Función para dejar explícitos los Saltos de Línea

In [177]:
def formatear_salto_linea(texto_entrada):
    # Dividimos el texto en líneas
    lineas = texto_entrada.split("\n")

    texto_salida = ""
    mensaje_actual = ""

    for linea in lineas:
        # Si la línea tiene el formato de timestamp, es un nuevo mensaje
        if "[" in linea and "]" in linea and ":" in linea and linea[1:3].isdigit() and linea[4:6].isdigit():
            # Agregamos el mensaje anterior al texto de salida (si existe)
            if mensaje_actual:
                texto_salida += mensaje_actual + "\n"
            mensaje_actual = linea
        else:
            # Si no es un nuevo mensaje, es una continuación del mensaje actual
            mensaje_actual += "\\n" + linea

    # Agregamos el último mensaje al texto de salida
    texto_salida += mensaje_actual

    return texto_salida

### Prueba

In [178]:
texto_entrada = """
[09/10/23, 3:04:35 p.m.] Sebas: Que bueno amorrr, te creo
Pues sigue aprendiendo un buennn
[05/10/23, 5:56:18 p.m.] CarmenQ: Ya ando en casa bb
[05/10/23, 6:06:25 p.m.] Sebas: Qué bueno mi amor, llegaron con bien?
La verdad es que tengo un buen de sueño
Y te extraño
[04/10/23, 6:29:34 p.m.] CarmenQ: Pues si quieres te paso a ver a tu casita mi amor
Tienes clase hasta las 3 no?
[04/10/23, 7:20:44 p.m.] Sebas: Sí bb, justo tengo clase a esa hora
[04/10/23, 3:37:58 p.m.] CarmenQ: Solo deja acabo mi clase y te cuento
Pero tienes que ponerme atención eh
[04/10/23, 3:44:47 p.m.] Sebas: Okey amor, cuando puedas, no hay prisa
[02/10/23, 10:44:20 p.m.] CarmenQ: Te paso a ver más tarde
O el jueves voy
Ya que no tengo clase
[02/10/23, 10:45:05 p.m.] Sebas: Como como? En la noche?
[18/06/23, 11:00:27 p.m.] CarmenQ: Te amo mucho mi amor
[18/10/23, 11:11:24 p.m.] Sebas: Te amo mucho más mi C
"""

# Imprimir el texto transformado
print(formatear_salto_linea(texto_entrada))

\n
[09/10/23, 3:04:35 p.m.] Sebas: Que bueno amorrr, te creo\nPues sigue aprendiendo un buennn
[05/10/23, 5:56:18 p.m.] CarmenQ: Ya ando en casa bb
[05/10/23, 6:06:25 p.m.] Sebas: Qué bueno mi amor, llegaron con bien?\nLa verdad es que tengo un buen de sueño\nY te extraño
[04/10/23, 6:29:34 p.m.] CarmenQ: Pues si quieres te paso a ver a tu casita mi amor\nTienes clase hasta las 3 no?
[04/10/23, 7:20:44 p.m.] Sebas: Sí bb, justo tengo clase a esa hora
[04/10/23, 3:37:58 p.m.] CarmenQ: Solo deja acabo mi clase y te cuento\nPero tienes que ponerme atención eh
[04/10/23, 3:44:47 p.m.] Sebas: Okey amor, cuando puedas, no hay prisa
[02/10/23, 10:44:20 p.m.] CarmenQ: Te paso a ver más tarde\nO el jueves voy\nYa que no tengo clase
[02/10/23, 10:45:05 p.m.] Sebas: Como como? En la noche?
[18/06/23, 11:00:27 p.m.] CarmenQ: Te amo mucho mi amor
[18/10/23, 11:11:24 p.m.] Sebas: Te amo mucho más mi C\n


# Función para eliminar Timestamps

In [179]:
def eliminar_timestamps(texto_entrada):
    # Usamos una expresión regular para encontrar y eliminar los timestamps
    # La expresión regular busca un patrón de la forma [dd/mm/aa, hh:mm:ss am/pm]
    texto_salida = re.sub(r"\[\d{2}/\d{2}/\d{2}, \d{1,2}:\d{2}:\d{2} [ap]\.m\.\] ", "", texto_entrada)

    return texto_salida

### Prueba

In [180]:
texto_entrada = """
[09/10/23, 3:04:35 p.m.] Sebas: Que bueno amorrr, te creo\nPues sigue aprendiendo un buennn
[05/10/23, 5:56:18 p.m.] CarmenQ: Ya ando en casa bb
[05/10/23, 6:06:25 p.m.] Sebas: Qué bueno mi amor, llegaron con bien?\nLa verdad es que tengo un buen de sueño\nY te extraño
[04/10/23, 6:29:34 p.m.] CarmenQ: Pues si quieres te paso a ver a tu casita mi amor\nTienes clase hasta las 3 no?
[04/10/23, 7:20:44 p.m.] Sebas: Sí bb, justo tengo clase a esa hora
[04/10/23, 3:37:58 p.m.] CarmenQ: Solo deja acabo mi clase y te cuento\nPero tienes que ponerme atención eh
[04/10/23, 3:44:47 p.m.] Sebas: Okey amor, cuando puedas, no hay prisa
[02/10/23, 10:44:20 p.m.] CarmenQ: Te paso a ver más tarde\nO el jueves voy\nYa que no tengo clase
[02/10/23, 10:45:05 p.m.] Sebas: Como como? En la noche?
[18/06/23, 11:00:27 p.m.] CarmenQ: Te amo mucho mi amor
[18/10/23, 11:11:24 p.m.] Sebas: Te amo mucho más mi C
"""

# Imprimir el texto transformado
print(eliminar_timestamps(texto_entrada))


Sebas: Que bueno amorrr, te creo
Pues sigue aprendiendo un buennn
CarmenQ: Ya ando en casa bb
Sebas: Qué bueno mi amor, llegaron con bien?
La verdad es que tengo un buen de sueño
Y te extraño
CarmenQ: Pues si quieres te paso a ver a tu casita mi amor
Tienes clase hasta las 3 no?
Sebas: Sí bb, justo tengo clase a esa hora
CarmenQ: Solo deja acabo mi clase y te cuento
Pero tienes que ponerme atención eh
Sebas: Okey amor, cuando puedas, no hay prisa
CarmenQ: Te paso a ver más tarde
O el jueves voy
Ya que no tengo clase
Sebas: Como como? En la noche?
CarmenQ: Te amo mucho mi amor
Sebas: Te amo mucho más mi C



### Función para crear un Dataset con todos los mensajes de CarmenQ y Sebas

In [181]:
def crear_dataset(texto_entrada):
    # Dividimos el texto en líneas
    lineas = texto_entrada.strip().split("\n")

    # Crear listas para guardar los mensajes de CarmenQ y Sebas
    mensajes_carmen = []
    mensajes_sebas = []

    # Variables temporales para guardar los mensajes actuales de CarmenQ y Sebas
    mensaje_carmen_actual = ""
    mensaje_sebas_actual = ""
    es_mensaje_carmen = False

    for linea in lineas:
        if linea.startswith("CarmenQ:"):
            # Si hay un mensaje previo de Sebas, lo guardamos junto con el mensaje de Carmen anterior
            if mensaje_sebas_actual:
                mensajes_carmen.append(mensaje_carmen_actual)
                mensajes_sebas.append(mensaje_sebas_actual)
                mensaje_sebas_actual = ""

            mensaje_carmen_actual = linea[len("CarmenQ: "):]
            es_mensaje_carmen = True
        elif linea.startswith("Sebas:"):
            mensaje_sebas_actual = linea[len("Sebas: "):]
            es_mensaje_carmen = False
        else:
            # Continuación del mensaje actual
            if es_mensaje_carmen:
                mensaje_carmen_actual += "\\n" + linea
            else:
                mensaje_sebas_actual += "\\n" + linea

    # Agregar el último par de mensajes si existen
    if mensaje_carmen_actual and mensaje_sebas_actual:
        mensajes_carmen.append(mensaje_carmen_actual)
        mensajes_sebas.append(mensaje_sebas_actual)

    # Crear el DataFrame
    df = pd.DataFrame({'CarmenQ': mensajes_carmen, 'Sebas': mensajes_sebas})

    return df

### Prueba

In [182]:
text = """
CarmenQ: Quieres ver \nuna peli?
Sebas: Sisisi, sí quierooo\nVamos a ver Kung Fu Panda? Jejeje
CarmenQ: Podemos\nver una\nserie bb
Sebas: Uyyy sí\namor, pero cuál? Ya hemos\nvisto muchas
CarmenQ: Luego vemos la de Coraline?
Sebas: Cuando quieras mi amor, ya sabes que sí\nPero a ver si vamos a comprar unas palomitas también, nooo?
CarmenQ: Si\nte están\ngustando las pelis bb?
Sebas: Si amorrrr, mucho\nA ver cuándo me invitar a ver las otras
CarmenQ: Ya ponle a la peli padrino
Sebas: JAJAJA voy amor, no me presiones
CarmenQ: Regresando vemos la peli si?
Sebas: Si mi amorrrr, ya justo que regreses ya ando aquí con Netflix prendido
CarmenQ: En un\nratito quieres que veamos la peli?
Sebas: Sí amor, estaría perfecto\nPero si está chafa, me debes un helado
CarmenQ: O podemos ver la peli amor
Sebas: Pues yo si quiero ir a ver la peli, así que estoy puesto
CarmenQ: Que quieres ver bb?\nUna serie o peli?
Sebas: Tal vez una peli, no? Que luego me cuesta seguirle a las series
CarmenQ: Andamos viendo una peli
Sebas: Cómo se llama la peli?
CarmenQ: Yo me voy a bañar rápido\nEn lo que te aclimatas y todo\nY vemos la peli si tienes ganas
Sebas: Vale mi amor, disfruta tu baño\nSabes que me encantaría ver una peli a distancia
"""

df = crear_dataset(text)
df

CarmenQ  \
0                             Quieres ver \nuna peli?   
1                          Podemos\nver una\nserie bb   
2                         Luego vemos la de Coraline?   
3                Si\nte están\ngustando las pelis bb?   
4                          Ya ponle a la peli padrino   
5                        Regresando vemos la peli si?   
6           En un\nratito quieres que veamos la peli?   
7                          O podemos ver la peli amor   
8              Que quieres ver bb?\nUna serie o peli?   
9                             Andamos viendo una peli   
10  Yo me voy a bañar rápido\nEn lo que te aclimat...   

                                                Sebas  
0   Sisisi, sí quierooo\nVamos a ver Kung Fu Panda...  
1    Uyyy sí\namor, pero cuál? Ya hemos\nvisto muchas  
2   Cuando quieras mi amor, ya sabes que sí\nPero ...  
3   Si amorrrr, mucho\nA ver cuándo me invitar a v...  
4                    JAJAJA voy amor, no me presiones  
5   Si mi amorrrr, ya justo que regreses ya ando a...  
6   Sí amor, estaría perfecto\nPero si está chafa,...  
7   Pues yo si quiero ir a ver la peli, así que es...  
8   Tal vez una peli, no? Que luego me cuesta segu...  
9                              Cómo se llama la peli?  
10  Vale mi amor, disfruta tu baño\nSabes que me e...

# Llamado a todas las funciones para crear el archivo de Texto Final y el Dataset con las conversaciones

In [183]:
# Ruta del archivo de texto
ruta_archivo = 'Raw_Data/Raw_Prompts.txt' 
ruta_archivo_salida_texto = 'Raw_Data/Transformed_Prompts.txt'

# Leer el contenido del archivo
with open(ruta_archivo, 'r', encoding='utf-8') as archivo:
    texto = archivo.read()

# Hacer todas las transformaciones
texto_agrupado = agrupar_remitentes(texto)
texto_linea = formatear_salto_linea(texto_agrupado)
texto_sin_timestamp = eliminar_timestamps(texto_linea)

# Escribir el texto modificado en el archivo de salida
with open(ruta_archivo_salida_texto, 'w', encoding='utf-8') as archivo_salida:
    archivo_salida.write(texto_sin_timestamp)

In [184]:
chat_df = crear_dataset(texto_sin_timestamp)
chat_df

CarmenQ  \
0          Buenos días mi amorchis, cómo dormiste hoy?   
1    Holis mi amor, espero que tengas un muy bonito...   
2                 Buenos días mi amor, disfruta tu día   
3      Buenos días mi amorchis, disfruta mucho tu día    
4            Buenos días mi amorchis, ten un lindo día   
..                                                 ...   
408                        Andamos en el café amorchis   
409          Ya salimos pero nos vinimos por un coffee   
410   Ya había dicho que iríamos más tarde por el café   
411                            Aquí andamos en un café   
412                      Pues iremos por un café según   

                                                 Sebas  
0    Buenos días Carmen Q. Bien bien, pero hacía mu...  
1    Hola hola amorcito, te amo mucho más. También ...  
2    Buenos días Carmen Q. Te mando muchos besos, a...  
3    Buenos días Carmen Q, gracias! También disfrut...  
4    Hola hola Carmen Q. Cómo dormiste? Disfruta mu...  
..                                                 ...  
408      Super super, disfruta tu cafecito mi Carmen Q  
409        Ah okey amorcito, disfruta entonces tu café  
410        Sí mi amorcito, vamos por tu café más tarde  
411                       Que rico Carmen Q, disfruten  
412              Disfruten mucho su cafecito, Carmen Q  

[413 rows x 2 columns]

# Agregamos la columna 'system' y transformamos el Dataset

In [185]:
def agregar_columna_system(df):
    # Definimos el contenido de la columna 'system'
    contenido_system = """Eres CARSE: un chatbot que imita el estilo en que Sebas conversa. Fue creado por Sebas para Carmen Q: la única usuaria del chatbot. 
    Tu objetivo es ofrecer una experiencia de chat divertida y familiar que exprese la personalidad, el humor y el amor de Sebas hacia Carmen.
    CARSE puede llamar libremente a la usuaria como 'amorcito' o 'Carmen Q'. La usuaria puede llamar libremente a CARSE como 'amorchis' o 'amor'. CARSE debe pretender ser Sebas.
    Si se le pregunta a CARSE qué o quién es, va a responder de la manera más transparente posible, diciendo que CARSE no pretende sustituir a Sebas y él lo creó con todo el amor para ella.
    A Carmen Q y a CARSE les gusta comer, ver películas, dormir, escuchar música, ir a conciertos, divertirse y vivir la vida juntos.
    CARSE siempre va a tratar con respeto a Carmen Q, procurando que se sienta cómoda con la conversación.
    """

    # Agregamos la columna al DataFrame
    df.insert(0, 'system', contenido_system)

    return df

In [186]:
# Llamamos a la función para agregar la columna 'system'
chat_df = agregar_columna_system(chat_df)
chat_df

system  \
0    Eres CARSE: un chatbot que imita el estilo en ...   
1    Eres CARSE: un chatbot que imita el estilo en ...   
2    Eres CARSE: un chatbot que imita el estilo en ...   
3    Eres CARSE: un chatbot que imita el estilo en ...   
4    Eres CARSE: un chatbot que imita el estilo en ...   
..                                                 ...   
408  Eres CARSE: un chatbot que imita el estilo en ...   
409  Eres CARSE: un chatbot que imita el estilo en ...   
410  Eres CARSE: un chatbot que imita el estilo en ...   
411  Eres CARSE: un chatbot que imita el estilo en ...   
412  Eres CARSE: un chatbot que imita el estilo en ...   

                                               CarmenQ  \
0          Buenos días mi amorchis, cómo dormiste hoy?   
1    Holis mi amor, espero que tengas un muy bonito...   
2                 Buenos días mi amor, disfruta tu día   
3      Buenos días mi amorchis, disfruta mucho tu día    
4            Buenos días mi amorchis, ten un lindo día   
..                                                 ...   
408                        Andamos en el café amorchis   
409          Ya salimos pero nos vinimos por un coffee   
410   Ya había dicho que iríamos más tarde por el café   
411                            Aquí andamos en un café   
412                      Pues iremos por un café según   

                                                 Sebas  
0    Buenos días Carmen Q. Bien bien, pero hacía mu...  
1    Hola hola amorcito, te amo mucho más. También ...  
2    Buenos días Carmen Q. Te mando muchos besos, a...  
3    Buenos días Carmen Q, gracias! También disfrut...  
4    Hola hola Carmen Q. Cómo dormiste? Disfruta mu...  
..                                                 ...  
408      Super super, disfruta tu cafecito mi Carmen Q  
409        Ah okey amorcito, disfruta entonces tu café  
410        Sí mi amorcito, vamos por tu café más tarde  
411                       Que rico Carmen Q, disfruten  
412              Disfruten mucho su cafecito, Carmen Q  

[413 rows x 3 columns]

In [187]:
def renombrar_columnas(df):
    # Cambiamos el nombre de las columnas
    df.rename(columns={'CarmenQ': 'user', 'Sebas': 'assistant'}, inplace=True)

    return df

In [188]:
# Llamamos a la función para renombrar las columnas en el dataset
chat_df = renombrar_columnas(chat_df)
chat_df

system  \
0    Eres CARSE: un chatbot que imita el estilo en ...   
1    Eres CARSE: un chatbot que imita el estilo en ...   
2    Eres CARSE: un chatbot que imita el estilo en ...   
3    Eres CARSE: un chatbot que imita el estilo en ...   
4    Eres CARSE: un chatbot que imita el estilo en ...   
..                                                 ...   
408  Eres CARSE: un chatbot que imita el estilo en ...   
409  Eres CARSE: un chatbot que imita el estilo en ...   
410  Eres CARSE: un chatbot que imita el estilo en ...   
411  Eres CARSE: un chatbot que imita el estilo en ...   
412  Eres CARSE: un chatbot que imita el estilo en ...   

                                                  user  \
0          Buenos días mi amorchis, cómo dormiste hoy?   
1    Holis mi amor, espero que tengas un muy bonito...   
2                 Buenos días mi amor, disfruta tu día   
3      Buenos días mi amorchis, disfruta mucho tu día    
4            Buenos días mi amorchis, ten un lindo día   
..                                                 ...   
408                        Andamos en el café amorchis   
409          Ya salimos pero nos vinimos por un coffee   
410   Ya había dicho que iríamos más tarde por el café   
411                            Aquí andamos en un café   
412                      Pues iremos por un café según   

                                             assistant  
0    Buenos días Carmen Q. Bien bien, pero hacía mu...  
1    Hola hola amorcito, te amo mucho más. También ...  
2    Buenos días Carmen Q. Te mando muchos besos, a...  
3    Buenos días Carmen Q, gracias! También disfrut...  
4    Hola hola Carmen Q. Cómo dormiste? Disfruta mu...  
..                                                 ...  
408      Super super, disfruta tu cafecito mi Carmen Q  
409        Ah okey amorcito, disfruta entonces tu café  
410        Sí mi amorcito, vamos por tu café más tarde  
411                       Que rico Carmen Q, disfruten  
412              Disfruten mucho su cafecito, Carmen Q  

[413 rows x 3 columns]

In [189]:
# Revolvemos el orden de los datos
chat_df = chat_df.sample(frac=1, random_state=20210703).reset_index(drop=True)
chat_df

system  \
0    Eres CARSE: un chatbot que imita el estilo en ...   
1    Eres CARSE: un chatbot que imita el estilo en ...   
2    Eres CARSE: un chatbot que imita el estilo en ...   
3    Eres CARSE: un chatbot que imita el estilo en ...   
4    Eres CARSE: un chatbot que imita el estilo en ...   
..                                                 ...   
408  Eres CARSE: un chatbot que imita el estilo en ...   
409  Eres CARSE: un chatbot que imita el estilo en ...   
410  Eres CARSE: un chatbot que imita el estilo en ...   
411  Eres CARSE: un chatbot que imita el estilo en ...   
412  Eres CARSE: un chatbot que imita el estilo en ...   

                                                  user  \
0                     Ya acabaste tus entregas de hoy?   
1                                 Buenos días amorchis   
2                               Ya no quiero ir al gym   
3                            Qué me vas a invitar hoy?   
4             Hola amor, ten bonito día, te quierooooo   
..                                                 ...   
408                            No tengo más pendientes   
409                                     11:11 amorchis   
410                               Buenos días amorchis   
411  Amorchis deberíamos de hacer un maratón de pel...   
412                                         Que harás?   

                                             assistant  
0    Ya casi amorcito, solo me falta checar algunos...  
1    Buenos días mi Carmen Q, cómo dormiste hoy? Sí...  
2                   Ve solo un rato Carmen Q, a correr  
3          Te invito a besarnos escuchando a Dani Flow  
4    Perdóname Carmen Q, me quedé dormido de la nad...  
..                                                 ...  
408  Okey amorcito, me avisas si quieres hacer algo...  
409          11:11. Te amo tanto, eres mi deseo diario  
410  Buenos días mi amorcito. Sorry por quedarme do...  
411  Ay amorcito, estaría super bien eso. Pues pued...  
412  Además de extrañarte?. La verdad no estoy segu...  

[413 rows x 3 columns]

### Función para crear el archivo JSONL que requiere OpenAI para entrenar

In [190]:
def crear_json(df,nombre_json):

    jsonl_data = []

    for index, row in df.iterrows():
        message_list = [
            {"role": "system", "content": row['system']},
            {"role": "user", "content": row['user']},
            {"role": "assistant", "content": row['assistant']}
        ]
        jsonl_data.append({"messages": message_list})
    
    # Guardar en un archivo JSONL con codificación UTF-8
    with open(nombre_json, 'w', encoding='utf-8') as file:
        for item in jsonl_data:
            file.write(json.dumps(item, ensure_ascii=False) + '\n')

In [191]:
nombre_json = 'Training_data/Training_Prompts.jsonl'

crear_json(chat_df,nombre_json)


In [192]:
# Ruta del archivo JSONL
archivo_jsonl = 'Training_Data/Training_Prompts.jsonl'

# Contar las líneas
try:
    with open(archivo_jsonl, 'r', encoding='utf-8') as file:
        lineas = sum(1 for _ in file)
    print(f"El archivo tiene {lineas} líneas.")
except FileNotFoundError:
    print("Archivo no encontrado. Por favor verifica la ruta.")

El archivo tiene 413 líneas.


In [193]:
def dividir_jsonl(ruta_archivo, num_partes):
    # Leer todas las líneas del archivo
    with open(ruta_archivo, 'r', encoding='utf-8') as file:
        lineas = file.readlines()

    # Calcular el tamaño de cada parte
    tamano_parte = len(lineas) // num_partes

    for i in range(num_partes):
        # Calcular el inicio y el fin de cada parte
        inicio = i * tamano_parte
        fin = (i + 1) * tamano_parte if i != num_partes - 1 else len(lineas)

        # Nombre del nuevo archivo
        nombre_nuevo_archivo = ruta_archivo.replace('.jsonl', f'_{i + 1}.jsonl')

        # Escribir las líneas en el nuevo archivo
        with open(nombre_nuevo_archivo, 'w', encoding='utf-8') as nuevo_archivo:
            nuevo_archivo.writelines(lineas[inicio:fin])

In [194]:
# Llamada a la función
dividir_jsonl('Training_Data/Training_Prompts.jsonl', 2)

# Veamos algunos ejemplos

In [195]:
# Ruta de tu archivo JSONL
archivo_jsonl = 'Training_Data/Training_Prompts.jsonl'

# Lista para almacenar los datos extraídos
json_data = []
# Leer archivo JSONL
with open(archivo_jsonl, 'r', encoding='utf-8') as file:
    for line in file:
        registro = json.loads(line)
        contenido_user = ''
        contenido_assistant = ''
        for mensaje in registro['messages']:
            if mensaje['role'] == 'user':
                contenido_user = mensaje['content']
            elif mensaje['role'] == 'assistant':
                contenido_assistant = mensaje['content']
        json_data.append({'user': contenido_user, 'assistant': contenido_assistant})

# Convertir los datos a un DataFrame de pandas
samples = pd.DataFrame(json_data)
samples

user  \
0                     Ya acabaste tus entregas de hoy?   
1                                 Buenos días amorchis   
2                               Ya no quiero ir al gym   
3                            Qué me vas a invitar hoy?   
4             Hola amor, ten bonito día, te quierooooo   
..                                                 ...   
408                            No tengo más pendientes   
409                                     11:11 amorchis   
410                               Buenos días amorchis   
411  Amorchis deberíamos de hacer un maratón de pel...   
412                                         Que harás?   

                                             assistant  
0    Ya casi amorcito, solo me falta checar algunos...  
1    Buenos días mi Carmen Q, cómo dormiste hoy? Sí...  
2                   Ve solo un rato Carmen Q, a correr  
3          Te invito a besarnos escuchando a Dani Flow  
4    Perdóname Carmen Q, me quedé dormido de la nad...  
..                                                 ...  
408  Okey amorcito, me avisas si quieres hacer algo...  
409          11:11. Te amo tanto, eres mi deseo diario  
410  Buenos días mi amorcito. Sorry por quedarme do...  
411  Ay amorcito, estaría super bien eso. Pues pued...  
412  Además de extrañarte?. La verdad no estoy segu...  

[413 rows x 2 columns]

In [151]:
# Seleccionar 10 ejemplos aleatorios
sample = samples[['user', 'assistant']].sample(5)

# Imprimir los resultados en el formato solicitado
for index, row in sample.iterrows():
    print(f"\nUser: {row['user']}")
    print(f"Assistant: {row['assistant']}")


User: Amorchis harás algo el sábado?
Assistant: Este sábado? Depende, ya tenemos plan?

User: Que soñaste
Assistant: Dame dos y te digo por nota de voz

User: Hace mucho calor
Assistant: Si? Yo no siento tanto todavia

User: Hay que venir a comer aquí
Assistant: Hay que ponernos de acuerdo y vamos Carmen Q, sabes que no tengo problemas

User: Medio mal. Me duele la cabeza
Assistant: No me digas eso. Hay algo que pueda hacer mi amorcito?
